In [13]:
%load_ext autoreload
%autoreload 2

import os
import sys
from pathlib import Path

project_root = Path.cwd()
sys.path.insert(0, str(project_root))

from prepare_params import prepare_production_params

print("Modules imported successfully")
print(f"Current working directory: {os.getcwd()}")


kml = "Sample Points\AfforestationSItesFixed.kml"
shp = "Sample Points\FieldPoints32_2018.shp"
tmx = "TMX\TML_pipeline_100mbuffer.kml"
cbc = "Sample Points\ColdwaterBCregion.kml"

print(kml)
print(shp)
print(tmx)
print(cbc)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Modules imported successfully
Current working directory: C:\Users\aradar\LEAF Files\LEAF_runner
Sample Points\AfforestationSItesFixed.kml
Sample Points\FieldPoints32_2018.shp
TMX\TML_pipeline_100mbuffer.kml
Sample Points\ColdwaterBCregion.kml


In [15]:
# TEMPLATE 1: Single Year Monthly Mosaics
# Use Case: Generate monthly mosaics for specific months in one year
# Example: Summer months (June, July, August) of 2023
# Customize these parameters as needed:

ProdParams = {
    # ============ REQUIRED PARAMETERS ============
    'sensor': 'S2_SR',                    # Sensor type
    'unit': 2,                   # A data unit code (1 or 2 for TOA or surface reflectance)    
    'nbYears': -1,            # positive int for annual product, or negative int for monthly product
    #'year': 2023,                          # CHANGE THIS: Year to process
    #'months': [8,9,10],                   # CHANGE THIS: Months to process (1-12)
    
    
    # ============ REGION PARAMETERS ============
    'regions':kml,  # CHANGE THIS: Path to your KML/SHP file
    'file_variables': ['TARGET_FID', 'AsssD_1', 'AsssD_2'], # CHANGE THIS: id, start_date, end_date (None for dates if they don't exist)
    #'file_variables': ['id', 'begin', 'end'],
    #'file_variables': ['system:index', None, None],
    'regions_start_index': 0,              # CHANGE THIS: Start at this region index
    'regions_end_index': 999,             # CHANGE THIS: End at this index (None = all)
    
    # ============ BUFFER PARAMETERS ============
    #'spatial_buffer_m': 0,             # UNCOMMENT & CHANGE: Buffer in meters around regions
    #'temporal_buffer': [[50, 90], [-10, 10], [100, 130]],          # UNCOMMENT & CHANGE: [days_before, days_after]
    'temporal_buffer': [["2020-05-01", "2020-05-31"]], #, ["2020-08-01", "2020-08-31"]],
    #'num_years': 3,
    
    
    # ============ OUTPUT PARAMETERS ============
    'resolution': 10,                      # Resolution in meters
    'projection': 'EPSG:3979',             # Coordinate projection
    'prod_names': ['fCOVER'],    #['LAI', 'FCOVER', 'fAPAR', 'Albedo'], 
    #'bands': ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22'],
    'out_folder': 'E:/S2_mosaics_runner_2026/afforestation/S2_may_2020_1000_regions_10m',
    'out_datatype': 'int16'
}

CompParams = {
  "number_workers":10,     
  "debug"       : True,
  "entire_tile" : False, 
  "nodes"       : 1,
  "node_memory" : "50G",
  'chunk_size': {'x': 512, 'y': 512}
}


print("\nconfigured")


configured


In [16]:
# Run the parameter preparation
result = prepare_production_params(ProdParams, CompParams)
'''
if result:
    print("\n" + "="*80)
    print(" SUCCESS - Parameters validated and ready!")
    print("="*80)
    print(f"\n Summary:")
    print(f"  Regions: {len(result['ProdParams']['regions'])}")
    print(f"  Time windows: {len(result['ProdParams']['start_dates'])}")
    print(f"  Total tasks: {len(result['ProdParams']['regions']) * len(result['ProdParams']['start_dates'])}")
    print(f"  Output folder: {result['ProdParams']['out_folder']}")
    print(f"\n Processing log saved to: {result['ProdParams']['out_folder']}/polygon_processing_log.csv")
    print("\n" + "="*80)
    print("Next step: Call Production.py with the validated parameters")
    print("="*80)
else:
    print("\n" + "="*80)
    print(" FAILED - Parameter validation failed")
    print("="*80)
    print("Check the error messages above for details.") '''


PARAMETER PREPARATION

Step 1/4: Validating input parameters...
✓ All parameters valid

Step 2/4: Loading regions from files...
<handle_regions_from_file> Detected file-based regions input: Sample Points\AfforestationSItesFixed.kml
<handle_regions_from_file> Loading regions...
<handle_regions_from_file> Region region639: Auto-generated end dates from start dates
<handle_regions_from_file> Region region373: Auto-generated end dates from start dates
<handle_regions_from_file> Region region313: Auto-generated end dates from start dates
<handle_regions_from_file> Region region915: Auto-generated end dates from start dates
<handle_regions_from_file> Region region698: Auto-generated start dates from end dates
<handle_regions_from_file> Region region167: Auto-generated start dates from end dates
<handle_regions_from_file> Region region98: Auto-generated end dates from start dates
<handle_regions_from_file> Region region912: Auto-generated end dates from start dates
<handle_regions_from_file>

'\nif result:\n    print("\n" + "="*80)\n    print(" SUCCESS - Parameters validated and ready!")\n    print("="*80)\n    print(f"\n Summary:")\n    print(f"  Regions: {len(result[\'ProdParams\'][\'regions\'])}")\n    print(f"  Time windows: {len(result[\'ProdParams\'][\'start_dates\'])}")\n    print(f"  Total tasks: {len(result[\'ProdParams\'][\'regions\']) * len(result[\'ProdParams\'][\'start_dates\'])}")\n    print(f"  Output folder: {result[\'ProdParams\'][\'out_folder\']}")\n    print(f"\n Processing log saved to: {result[\'ProdParams\'][\'out_folder\']}/polygon_processing_log.csv")\n    print("\n" + "="*80)\n    print("Next step: Call Production.py with the validated parameters")\n    print("="*80)\nelse:\n    print("\n" + "="*80)\n    print(" FAILED - Parameter validation failed")\n    print("="*80)\n    print("Check the error messages above for details.") '

In [17]:
# View processing log (if pandas is available)
try:
    import pandas as pd
    if result and result['processing_log'] is not None:
        print("\n Processing Log Preview:")
        print("=" * 80)
        display(result['processing_log'].head(10))
        print(f"\nTotal entries: {len(result['processing_log'])}")
except ImportError:
    print("pandas not available - install it to view the processing log in this cell")
    print("You can still view the CSV file directly in the output folder")


 Processing Log Preview:


region_id   area_m2  will_process status skip_reason
0   region0  14612.87          True  VALID         N/A
1   region1   4831.99          True  VALID         N/A
2   region2  36573.20          True  VALID         N/A
3   region3  54608.59          True  VALID         N/A
4   region4  32682.04          True  VALID         N/A
5   region5   9456.33          True  VALID         N/A
6   region6  27681.04          True  VALID         N/A
7   region7  43163.54          True  VALID         N/A
8   region8  44066.86          True  VALID         N/A
9   region9  15764.26          True  VALID         N/A


Total entries: 1000


In [18]:
import os
import sys
import geopandas as gpd

#Get the absolute path to the parent of current working directory 
cwd    = os.getcwd()
source_path = os.path.join(cwd, 'source')
sys.path.append(source_path)
sys.path

from Production import main

print(ProdParams)

{'sensor': 'S2_SR', 'unit': 2, 'nbYears': -1, 'regions': {'region0': {'type': 'Polygon', 'coordinates': [[[-81.0143277776703, 44.792849553362], [-81.013046437586, 44.7928810241213], [-81.0130828894072, 44.7920357810087], [-81.0134196694422, 44.7918539873173], [-81.013283176937, 44.7913976888643], [-81.0142442205963, 44.7913333551658], [-81.0143277776703, 44.792849553362]]]}, 'region1': {'type': 'Polygon', 'coordinates': [[[-80.2866384110016, 44.3533435417762], [-80.2864858239462, 44.353000698271], [-80.2868313289172, 44.3529866183925], [-80.2871254773415, 44.3529366809224], [-80.2874977225433, 44.3529180592246], [-80.2876405698119, 44.3529059627622], [-80.2879206306362, 44.3528989373857], [-80.2880395541161, 44.3528827993289], [-80.2880782566738, 44.352880279965], [-80.2882027280036, 44.353154957613], [-80.288085927134, 44.3531261618167], [-80.287951530048, 44.3531125098555], [-80.2878832692439, 44.3531281508011], [-80.287738989293, 44.3532215337679], [-80.2877249039523, 44.35326444725

In [19]:
main(ProdParams, CompParams)


<get_time_window> one of required keys is not exist to form time.
<LEAF_production> All input parameters =  {'sensor': 'S2_SR', 'unit': 2, 'nbYears': -1, 'regions': {'region0': {'type': 'Polygon', 'coordinates': [[[-81.0143277776703, 44.792849553362], [-81.013046437586, 44.7928810241213], [-81.0130828894072, 44.7920357810087], [-81.0134196694422, 44.7918539873173], [-81.013283176937, 44.7913976888643], [-81.0142442205963, 44.7913333551658], [-81.0143277776703, 44.792849553362]]]}, 'region1': {'type': 'Polygon', 'coordinates': [[[-80.2866384110016, 44.3533435417762], [-80.2864858239462, 44.353000698271], [-80.2868313289172, 44.3529866183925], [-80.2871254773415, 44.3529366809224], [-80.2874977225433, 44.3529180592246], [-80.2876405698119, 44.3529059627622], [-80.2879206306362, 44.3528989373857], [-80.2880395541161, 44.3528827993289], [-80.2880782566738, 44.352880279965], [-80.2882027280036, 44.353154957613], [-80.288085927134, 44.3531261618167], [-80.287951530048, 44.3531125098555], [-

C:\Users\aradar\AppData\Local\anaconda3\envs\leaftoolbox2\Lib\site-packages\distributed\client.py:3164: UserWarning: Sending large graph of size 12.35 MiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(



<one_mosaic> Final mosaic bands: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'SZA', 'SAA', 'VZA', 'VAA']

<<<<<<<<<< Complete saving composite images >>>>>>>>>


<<<<<< The total elapsed time for mosaic generation =   1.15 minutes >>>>>>
File 'E:\S2_mosaics_runner_2026\afforestation\S2_may_2020_1000_regions_10m\log_6e5caf6f-02eb-4e80-b146-8b54e95a4bb5.out' does not exist.
Directory 'E:\S2_mosaics_runner_2026\afforestation\S2_may_2020_1000_regions_10m\dask_spill_6e5caf6f-02eb-4e80-b146-8b54e95a4bb5' and its contents have been deleted.

<create_LEAF_maps> The bands in mosaic image: Data variables:
    blue      (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
    green     (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
    red       (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
    rededge1  (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
  

C:\Users\aradar\LEAF Files\LEAF_runner\source\SL2P_NetsTools.py:160: UserWarning: Land cover values [0] not found in mapping dictionary. Mapping these to network ID 0. Mapped LC classes: [1, 3, 4, 17, 7, 8, 5, 11, 9, 15, 13, 2, 14, 10, 12, 18, 16, 19, 6]
  warnings.warn(f"Land cover values {unmapped_values} not found in mapping dictionary. "



<create_LEAF_maps> Bands in mosaic before rescaling: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'cosSZA', 'cosVZA', 'cosRAA']
<create_LEAF_maps> Bands in ready_mosaic after rescaling: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'cosSZA', 'cosVZA', 'cosRAA']
<estimate_VParams> the bands in DS options =  ['cosVZA', 'cosSZA', 'cosRAA', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22']
<invalidInput> Generating sl2p input data flag
Generating sl2p output product flag


<<< The elapsed time for generating one monthly tile product = 1.2007046500841776 minutes>>>


<export_VegParamMaps> the data variables in given VP map:  Data variables:
    date     (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
    fCOVER   (y, x) float32 1kB dask.array<chunksize=(21, 13), meta=np.ndarray>
    QC       (y, x) float32

...

C:\Users\aradar\AppData\Local\anaconda3\envs\leaftoolbox2\Lib\site-packages\distributed\client.py:3164: UserWarning: Sending large graph of size 12.35 MiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(



<one_mosaic> Final mosaic bands: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'SZA', 'SAA', 'VZA', 'VAA']

<<<<<<<<<< Complete saving composite images >>>>>>>>>


<<<<<< The total elapsed time for mosaic generation =   0.96 minutes >>>>>>
File 'E:\S2_mosaics_runner_2026\afforestation\S2_may_2020_1000_regions_10m\log_73cd47e9-fd21-4e4e-a8c8-07d63c64c0c8.out' does not exist.
Directory 'E:\S2_mosaics_runner_2026\afforestation\S2_may_2020_1000_regions_10m\dask_spill_73cd47e9-fd21-4e4e-a8c8-07d63c64c0c8' and its contents have been deleted.

<create_LEAF_maps> The bands in mosaic image: Data variables:
    blue      (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
    green     (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
    red       (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
    rededge1  (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
  

C:\Users\aradar\LEAF Files\LEAF_runner\source\SL2P_NetsTools.py:160: UserWarning: Land cover values [0] not found in mapping dictionary. Mapping these to network ID 0. Mapped LC classes: [1, 3, 4, 17, 7, 8, 5, 11, 9, 15, 13, 2, 14, 10, 12, 18, 16, 19, 6]
  warnings.warn(f"Land cover values {unmapped_values} not found in mapping dictionary. "



<create_LEAF_maps> Bands in mosaic before rescaling: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'cosSZA', 'cosVZA', 'cosRAA']
<create_LEAF_maps> Bands in ready_mosaic after rescaling: ['blue', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22', 'scl', 'date', 'score', 'cosSZA', 'cosVZA', 'cosRAA']
<estimate_VParams> the bands in DS options =  ['cosVZA', 'cosSZA', 'cosRAA', 'green', 'red', 'rededge1', 'rededge2', 'rededge3', 'nir08', 'swir16', 'swir22']
<invalidInput> Generating sl2p input data flag
Generating sl2p output product flag


<<< The elapsed time for generating one monthly tile product = 0.973321803410848 minutes>>>


<export_VegParamMaps> the data variables in given VP map:  Data variables:
    date     (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
    fCOVER   (y, x) float32 1kB dask.array<chunksize=(20, 14), meta=np.ndarray>
    QC       (y, x) float32 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

